

# 並列化の容易さ

:func:`optuna.study.Study.optimize` の並列化は簡単です。

手動で Optuna の最適化を実行したい場合：

    1. RDB サーバーを起動（この例では MySQL を使用）
    2. ``--storage`` 引数でスタディを作成
    3. 複数ノード/プロセス間でスタディを共有

もちろん、[Kubernetes の例](https://github.com/optuna/optuna-examples/tree/main/kubernetes)_ のように Kubernetes も利用可能です。

Optuna の並列最適化の動作を確認するには、以下の動画をご覧ください。

.. raw:: html

    <iframe width="560" height="315" src="https://www.youtube-nocookie.com/embed/J_aymk4YXhg?start=427" frameborder="0" allow="accelerometer; autoplay; encrypted-media; gyroscope; picture-in-picture" allowfullscreen></iframe>


## スタディの作成

``optuna create-study`` コマンドでスタディを作成できます。
Python スクリプトでは :func:`optuna.create_study` を使用します。


```bash
$ mysql -u root -e "CREATE DATABASE IF NOT EXISTS example"
$ optuna create-study --study-name "distributed-example" --storage "mysql://root@localhost/example"
[I 2020-07-21 13:43:39,642] A new study created with name: distributed-example
```
次に、最適化スクリプトを作成します。``foo.py`` に以下のコードがあると仮定します。

```python
import optuna


def objective(trial):
    x = trial.suggest_float("x", -10, 10)
    return (x - 2) ** 2


if __name__ == "__main__":
    study = optuna.load_study(
        study_name="distributed-example", storage="mysql://root@localhost/example"
    )
    study.optimize(objective, n_trials=100)
```
## 複数ノード/プロセス間でスタディを共有

最後に、共有したスタディを複数プロセスで実行します。
例えば、1つのターミナルで ``Process 1`` を実行し、別のターミナルで ``Process 2`` を実行します。
共有されたトライアル履歴に基づいてパラメータ提案が行われます。

Process 1:

```bash
$ python foo.py
[I 2020-07-21 13:45:02,973] Trial 0 finished with value: 45.35553104173011 and parameters: {'x': 8.73465151598285}. Best is trial 0 with value: 45.35553104173011.
[I 2020-07-21 13:45:04,013] Trial 2 finished with value: 4.6002397305938905 and parameters: {'x': 4.144816945707463}. Best is trial 1 with value: 0.028194513284051464.
...
```
Process 2（Process 1と同じコマンド）:

```bash
$ python foo.py
[I 2020-07-21 13:45:03,748] Trial 1 finished with value: 0.028194513284051464 and parameters: {'x': 1.8320877810162361}. Best is trial 1 with value: 0.028194513284051464.
[I 2020-07-21 13:45:05,783] Trial 3 finished with value: 24.45966755098074 and parameters: {'x': 6.945671597566982}. Best is trial 1 with value: 0.028194513284051464.
...
```
<div class="alert alert-info"><h4>Note</h4><p>``n_trials`` は各プロセスが実行するトライアル数であり、全プロセスの合計トライアル数ではありません。上記のスクリプトでは各プロセスで100トライアル、合計200トライアル（100トライアル×2プロセス）を実行します。:class:`optuna.study.MaxTrialsCallback` を使用すると、全プロセスでのトライアル実行回数を制御できます。</p></div>

<div class="alert alert-info"><h4>Note</h4><p>大規模分散最適化では SQLite の使用は推奨しません。デッドロックや深刻なパフォーマンス問題が発生する可能性があります。PostgreSQL や MySQL などの他のデータベースエンジンの使用を検討してください。</p></div>

<div class="alert alert-info"><h4>Note</h4><p>分散最適化時に SQLite データベースを NFS に置くことは避けてください。詳細は https://www.sqlite.org/faq.html#q5 も参照してください。</p></div>
